In [4]:
import numpy as np
import scipy.stats as stats
from tqdm import tnrange, tqdm_notebook

from allensdk.core.brain_observatory_cache import BrainObservatoryCache

#Plotting tools
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
from plotly.graph_objs import Scatter, Figure, Layout

from force import NeuralNetwork
from force import Simulation


init_notebook_mode(connected=True)

In [31]:
#boc = BrainObservatoryCache(manifest_file='/Users/elijahc/dev/allen-assistant/boc/manifest.json')
boc = BrainObservatoryCache(manifest_file='/home/elijahc/dev/tools/allen-assistant/boc/manifest.json')

exps = boc.get_ophys_experiments(
    imaging_depths=[175],
    targeted_structures=['VISp'],
    cre_lines=['Cux2-CreERT2'],
    stimuli=['natural_scenes'])

In [32]:
def rolling_window(a, window):
    shape = a.shape[:-1] + (a.shape[-1] - window + 1, window)
    strides = a.strides + (a.strides[-1],)
    return np.lib.stride_tricks.as_strided(a, shape=shape, strides=strides)

def train_force(cell_ids,data_set,net,idx_table,num_train=1000,num_test=200,win=0):
    max_len = num_train+num_test
    t,dff = data_set.get_dff_traces(cell_specimen_ids=cell_ids)
    dff = dff[:,idx_table['start'].item():idx_table['end'].item()].astype(np.float32)
    t = t[idx_table['start'].item():idx_table['end'].item()].astype(np.float32)
    dt = np.around((np.roll(t,-1)-t)[:-1].mean(),decimals=5)
    sim = Simulation(net,dt=dt)
    sim.ft = dff[:,:max_len].T
    sim.timeline=t[:max_len]
    sim.run('training',t_begin=0,t_end=num_train)
    zt1 = sim.zt
    sim.run('testing',train=False,t_begin=num_train,t_end=max_len)
    zt2 = sim.zt
    sim.zt = np.concatenate([zt1,zt2])
    
    return sim

exp_id = exps[1]['id']
data_set = boc.get_ophys_experiment_data(exp_id)
cids = data_set.get_cell_specimen_ids()
print('Experiment ID: %d' % exp_id)
print('Number of Cells: %d'%len(cids))

idxs = data_set.get_spontaneous_activity_stimulus_table()

net = NeuralNetwork(N=1000,num_fits=100)
n_train=7000
n_test=1000
sim = train_force(cell_ids=cids[:100],
                  data_set=data_set,
                  net=net,
                  idx_table=idxs,
                  num_train=n_train,
                  num_test=n_test,win=4)

Experiment ID: 500964514
Number of Cells: 214
(8000, 100)


In [25]:
ts1 = sim.timeline
ft_full =[]
zt_full =[]
ft_test_data = []
zt_test_data = []
print(sim.ft.shape)
print(sim.zt.shape)
for i in np.arange(sim.ft.shape[1]):
    fti = Scatter(
        x=ts1,
        y=sim.ft[:,i],
        mode='lines',
        name='ft%d'%i)
    zti = Scatter(
        x=ts1,
        y=sim.zt[:,i],
        mode='lines',
        name='zt%d'%i)
    ft_full.append(fti)
    zt_full.append(zti)
    
    ft_testi = Scatter(
        x=sim.timeline[n_train:],
        y=sim.ft[n_train:,i],
        mode='lines',
        name='ft_test_%d'%i
    )
    zt_testi = Scatter(
        x=sim.timeline[n_train:],
        y=sim.zt[n_train:,i],
        mode='lines',
        name='zt_test_%d'%i
    )
    ft_test_data.append(ft_testi)
    zt_test_data.append(zt_testi)
sse = []
corr = []
fevs = []
for f,z in zip(ft_test_data,zt_test_data):
    diff = f.y - z.y
    se = np.power(diff,2)
    error.append(se.sum())
    
    fev = 1 - (se.mean()/np.var(f.y))
    fevs.append(fev)
    
    R,pv = stats.pearsonr(f.y,z.y)
    corr.append(R)
print('Error Matrix Shape: ',str(np.array(sse).shape))
print('Pearson Corr. Matrix Shape: ',str(np.array(corr).shape))

# Layout Definitions
error_layout = Layout(
    title='Pearson Corr. Coef. by cell',

    yaxis=dict(
        title='Pearson Corr. Coef. (R)',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
)

force_layout = Layout(
    title='Force Layout Default Title',
    xaxis=dict(
        title='Time(s)',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
    yaxis=dict(
        title='dF/F (a.u.)',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
)

(8000, 100)
(8000, 100)
('Error Matrix Shape: ', '(0,)')
('Pearson Corr. Matrix Shape: ', '(100,)')


In [26]:

error_fig = Figure(data=[{'y':np.array(fevs)}],layout=error_layout)
iplot(error_fig)

#iplot([ft2,zt2])

In [27]:
idx = 9

fl_full = fl_test = force_layout
fl_full.title='Full Training Time Trace'
fl_test.title='Testing Period Time Trace'

iplot(Figure(data=[ft_full[idx],zt_full[idx]],
             layout=force_layout)
     )
iplot(Figure(
    data=[ft_test_data[idx],zt_test_data[idx]],
    layout=force_layout)
     )

In [29]:
# Smallest Error plot
idx = np.argmin(fevs)
print('Smallest Error: Cell %d'%idx)

fl_full = fl_test = force_layout
fl_full.title='Full Training Time Trace'
fl_test.title='Testing Period Time Trace'

iplot(Figure(data=[ft_full[idx],zt_full[idx]],
             layout=force_layout)
     )
iplot(Figure(
    data=[ft_test_data[idx],zt_test_data[idx]],
    layout=force_layout)
     )


Smallest Error: Cell 34


In [30]:
# Maximum Error plot
idx = np.argmax(fevs)
print('Largest Error: Cell %d'%idx)
fl_full = fl_test = force_layout

fl_full.title='Full Training Time Trace'
iplot(Figure(data=[ft_full[idx],zt_full[idx]],
             layout=fl_full)
     )
fl_test.title='Testing Period Time Trace'
iplot(Figure(
    data=[ft_test_data[idx],zt_test_data[idx]],
    layout=fl_test)
     )


Largest Error: Cell 9
